# 1 libraries

In [1]:
import numpy as np
import pandas as pd
import os
import re
import networkx as nx
import scona as scn
import pickle
from numpy import genfromtxt

# 2 load connectivity matrix

In [2]:
data_dir = '/home/ubuntu/Stella/MLVU multimodality/valid_DTI_con_mat_1105'

In [3]:
targ_folder = os.listdir(data_dir)

In [4]:
con_mat_list=list(targ_folder)

In [5]:
len(con_mat_list)

2085

# 3 coordinate & brain name & centroids

In [6]:
coordinate = pd.read_csv('DTI node coordinate - Done.csv')

In [7]:
brain_name = coordinate.iloc[:, 1].tolist()

In [8]:
brain_name

['ctx-lh-superiorfrontal',
 'ctx-rh-superiorparietal',
 'Right-Caudate',
 'ctx-lh-inferiortemporal',
 'ctx-rh-insula',
 'ctx-rh-rostralanteriorcingulate',
 'ctx-rh-supramarginal',
 'ctx-rh-entorhinal',
 'ctx-lh-fusiform',
 'ctx-rh-superiortemporal',
 'ctx-lh-middletemporal',
 'ctx-rh-bankssts',
 'ctx-rh-inferiorparietal',
 'ctx-rh-fusiform',
 'ctx-rh-caudalanteriorcingulate',
 'ctx-rh-inferiortemporal',
 'Left-Cerebellum-Cortex',
 'ctx-lh-caudalmiddlefrontal',
 'ctx-lh-bankssts',
 'Left-Accumbens-area',
 'Right-Pallidum',
 'Left-Hippocampus',
 'ctx-lh-superiortemporal',
 'ctx-lh-rostralanteriorcingulate',
 'ctx-rh-middletemporal',
 'Left-Amygdala',
 'ctx-rh-caudalmiddlefrontal',
 'ctx-rh-pericalcarine',
 'ctx-rh-parahippocampal',
 'Left-Caudate',
 'ctx-rh-postcentral',
 'ctx-lh-parsopercularis',
 'ctx-rh-lingual',
 'ctx-lh-lateraloccipital',
 'ctx-lh-isthmuscingulate',
 'ctx-lh-parstriangularis',
 'ctx-lh-rostralmiddlefrontal',
 'ctx-lh-postcentral',
 'ctx-rh-rostralmiddlefrontal',
 'c

In [9]:
centroids = coordinate.iloc[:, 4:]
centroids_ = centroids.to_numpy()
centroids_list = []
for i in range (centroids_.shape[0]):
    centroids_list.append(centroids_[i]) 

# 4 label

In [7]:
label = pd.read_csv('DTI_label.csv')

# 5 node_feat & num_nodes

In [8]:
num_nodes=84

In [9]:
node_skeleton = pd.read_csv('DTI - sMRI.csv')

In [11]:
node_data = pd.read_csv('mor.some.qc.csv')

In [12]:
node_data['subjectkey'] = node_data['subjectkey'].apply(lambda x : x.replace('_','')) #remove _ from subjectkey

In [13]:
node_skeleton_array  = np.array(node_skeleton.iloc[:, 2:])

In [14]:
node_skeleton_array.shape

(84, 2)

In [15]:
def node_feat_func(subject_id):
    node_feat = list()
    data = node_data[node_data['subjectkey'] == subject_id]
    for i in range (84):
        for j in range(2):
            col_name = node_skeleton_array[i][j]
            if pd.isna(col_name) == True:
                node_feat.append('nan')
            else:
                node_feat.append(data[col_name].values[0])
    return (np.array(node_feat)).reshape(84,2)

# 6 edge_feat & num_edges

In [16]:
def edge_list_func(adjacency):
    edge_list=[]
    for i in range (84):
        for j in range (84):
            edge_list.append((i, j, adjacency[i][j]))
                
    edge_new_list=[]
    for i in range (len(edge_list)):
        if edge_list[i][2] != 0:
            edge_new_list.append(edge_list[i])
            
    return edge_list

In [17]:
def num_edges_func(edge_list):
    num_edges=len(edge_list)
    return num_edges

In [18]:
def edge_feat_func(num_edges, edge_list):
    # initialization
    edgefeat_dim = 1
    edge_feat = np.zeros((int(num_edges), edgefeat_dim))
    edge_index = np.zeros((2, int(num_edges)))
    # calculation
    for i in range (num_edges):
        source = edge_list[i][0]
        target = edge_list[i][1]
        edge = edge_list[i][2]
        edge_index[0][i] = source
        edge_index[1][i] = target
        edge_feat[i] = edge
    return edge_feat, edge_index

#  generate brain graph

In [19]:
len(con_mat_list)

2085

In [22]:
for i in range(len(con_mat_list)):
    # load data
    data = os.path.join(data_dir, con_mat_list[i])
    subject_id = con_mat_list[i].split(' ')[4].split('.')[0]
    
    # make adjacency matrix
    mydata = genfromtxt(data, delimiter=',')
    adjacency = mydata[1:,1:]
    
    # label 
    intelligence = 0
    for i in range(len(label)):
        if label['subjectkey'][i] == subject_id:
            intelligence+=label['nihtbx_totalcomp_uncorrected'][i]
    
    # edge_index, edge_feat (raw)
    raw_edge_list = edge_list_func(adjacency)
    raw_num_edges = num_edges_func(raw_edge_list)
    raw_edge_feat, raw_edge_index = edge_feat_func(raw_num_edges, raw_edge_list)
    
    # edge_index, edge_feat (processed)
    zero_edge_index=[]
    for i, k in enumerate(raw_edge_feat):
        if k[0] == 0:
            zero_edge_index.append(i)
            
    edge_feat = np.delete(raw_edge_feat, zero_edge_index)
    node_from = np.delete(raw_edge_index[0], zero_edge_index)
    node_to = np.delete(raw_edge_index[1], zero_edge_index)
    edge_index = np.concatenate((node_from, node_to)).reshape(2, -1)
    num_edges = len(node_from)    
            
    # node_feat
    node_feat = node_feat_func(subject_id)
    
    # draw graph
    graph = dict({'labels': intelligence, 'num_nodes': num_nodes, 'num_edges': num_edges,
                                  'edge_index': edge_index, 'edge_feat': edge_feat,
                                  'node_feat': node_feat})
    
    print(graph)
    
    with open('/home/ubuntu/Stella/MLVU multimodality/final_structural_graph/structural_graph_%s.pickle'%subject_id, 'wb') as file:
        pickle.dump(graph, file)

{'labels': 0.413314432, 'num_nodes': 84, 'num_edges': 4768, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 79., 80., 83.]]), 'edge_feat': array([1.        , 0.60060605, 0.59795769, ..., 0.52088273, 0.52777567,
       1.        ]), 'node_feat': array([['3.1860000000000004', '28360.0'],
       ['2.5869999999999997', '17028.0'],
       ['nan', '4011.9'],
       ['2.929', '12030.0'],
       ['3.228', '7876.0'],
       ['3.0580000000000003', '2661.0'],
       ['2.9', '13071.0'],
       ['3.0439999999999996', '1911.0'],
       ['2.842', '10121.0'],
       ['3.113', '14661.0'],
       ['3.147', '13518.0'],
       ['2.799', '2757.0'],
       ['2.875', '19635.0'],
       ['2.975', '10886.0'],
       ['2.863', '3156.0'],
       ['3.0589999999999997', '13421.0'],
       ['nan', '60463.7'],
       ['2.8819999999999997', '8648.0'],
       ['2.9139999999999997', '3767.0'],
       ['nan', '525.8'],
       ['nan', '1970.8'],
       ['nan', '4289.1'],
       ['3.1

{'labels': 0.303898093, 'num_nodes': 84, 'num_edges': 4360, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 80., 82., 83.]]), 'edge_feat': array([1.        , 0.58723102, 0.55087653, ..., 0.4432736 , 0.6341992 ,
       1.        ]), 'node_feat': array([['2.965', '30505.0'],
       ['2.359', '16333.0'],
       ['nan', '3815.7'],
       ['2.887', '14219.0'],
       ['3.063', '9696.0'],
       ['2.95', '2434.0'],
       ['2.7289999999999996', '12512.0'],
       ['3.1430000000000002', '1735.0'],
       ['2.784', '11154.0'],
       ['3.0839999999999996', '16391.0'],
       ['2.925', '13820.0'],
       ['2.7939999999999996', '3021.0'],
       ['2.6319999999999997', '20356.0'],
       ['2.884', '10875.0'],
       ['2.543', '2530.0'],
       ['2.8369999999999997', '14654.0'],
       ['nan', '63336.1'],
       ['2.9330000000000003', '10308.0'],
       ['2.485', '2514.0'],
       ['nan', '558.0'],
       ['nan', '1801.0'],
       ['nan', '3854.7'],
       ['2

{'labels': -0.462016279, 'num_nodes': 84, 'num_edges': 4120, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 79., 80., 83.]]), 'edge_feat': array([1.        , 0.54309703, 0.5508174 , ..., 0.34728484, 0.35883947,
       1.        ]), 'node_feat': array([['3.1860000000000004', '33799.0'],
       ['2.593', '19194.0'],
       ['nan', '3676.7'],
       ['2.906', '15275.0'],
       ['3.237', '8968.0'],
       ['3.048', '3161.0'],
       ['2.918', '12928.0'],
       ['3.159', '1607.0'],
       ['3.02', '12280.0'],
       ['3.2439999999999998', '15287.0'],
       ['3.0860000000000003', '15018.0'],
       ['2.819', '2509.0'],
       ['2.7739999999999996', '25202.0'],
       ['2.947', '12523.0'],
       ['3.0210000000000004', '3238.0'],
       ['3.012', '14097.0'],
       ['nan', '64344.7'],
       ['2.963', '9779.0'],
       ['2.733', '3684.0'],
       ['nan', '606.5'],
       ['nan', '1887.1'],
       ['nan', '4147.7'],
       ['3.1660000000000004', '17709

{'labels': -0.024350922999999997, 'num_nodes': 84, 'num_edges': 5012, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 81., 82., 83.]]), 'edge_feat': array([1.        , 0.54530285, 0.603002  , ..., 0.72080064, 0.48004049,
       1.        ]), 'node_feat': array([['3.1439999999999997', '26418.0'],
       ['2.577', '15078.0'],
       ['nan', '3744.1'],
       ['2.9610000000000003', '11113.0'],
       ['3.17', '6608.0'],
       ['2.931', '2390.0'],
       ['2.947', '12060.0'],
       ['3.5589999999999997', '1588.0'],
       ['2.964', '8942.0'],
       ['3.133', '12805.0'],
       ['3.162', '13133.0'],
       ['3.0580000000000003', '3128.0'],
       ['2.8710000000000004', '16478.0'],
       ['2.8569999999999998', '9141.0'],
       ['2.8510000000000004', '2571.0'],
       ['3.0610000000000004', '10012.0'],
       ['nan', '48632.9'],
       ['2.8560000000000003', '8311.0'],
       ['2.681', '3932.0'],
       ['nan', '560.3'],
       ['nan', '1634.1'],
   

{'labels': 0.19448175399999998, 'num_nodes': 84, 'num_edges': 4430, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 80., 81., 83.]]), 'edge_feat': array([1.        , 0.57183507, 0.61048688, ..., 0.51527029, 0.62392888,
       1.        ]), 'node_feat': array([['2.986', '30736.0'],
       ['2.376', '14244.0'],
       ['nan', '4108.2'],
       ['2.747', '13256.0'],
       ['3.028', '8507.0'],
       ['2.912', '2377.0'],
       ['2.844', '13236.0'],
       ['3.008', '1625.0'],
       ['2.675', '9892.0'],
       ['2.958', '12935.0'],
       ['3.0210000000000004', '14093.0'],
       ['2.56', '1887.0'],
       ['2.699', '17724.0'],
       ['2.735', '9496.0'],
       ['2.69', '2331.0'],
       ['2.801', '13014.0'],
       ['nan', '60493.4'],
       ['2.721', '8993.0'],
       ['2.845', '3034.0'],
       ['nan', '533.4'],
       ['nan', '1895.1'],
       ['nan', '3858.2'],
       ['3.158', '15838.0'],
       ['2.905', '3068.0'],
       ['3.0460000000000003

...

{'labels': -0.024350922999999997, 'num_nodes': 84, 'num_edges': 4530, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 79., 80., 83.]]), 'edge_feat': array([1.        , 0.5660736 , 0.57894075, ..., 0.53355699, 0.44684527,
       1.        ]), 'node_feat': array([['3.109', '27253.0'],
       ['2.556', '17432.0'],
       ['nan', '3926.1'],
       ['3.016', '11380.0'],
       ['3.1860000000000004', '7222.0'],
       ['2.888', '1611.0'],
       ['2.864', '14779.0'],
       ['3.7110000000000003', '1618.0'],
       ['2.905', '8946.0'],
       ['3.0439999999999996', '14509.0'],
       ['3.014', '13411.0'],
       ['3.238', '3063.0'],
       ['2.8080000000000003', '16187.0'],
       ['3.109', '9967.0'],
       ['2.696', '2185.0'],
       ['2.995', '9584.0'],
       ['nan', '62652.7'],
       ['2.965', '7922.0'],
       ['2.7680000000000002', '2833.0'],
       ['nan', '626.4'],
       ['nan', '1926.5'],
       ['nan', '3917.3'],
       ['3.003', '14108.0'],


{'labels': -1.5561796680000002, 'num_nodes': 84, 'num_edges': 4092, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 79., 80., 83.]]), 'edge_feat': array([1.        , 0.60906241, 0.63900146, ..., 0.48965425, 0.54052081,
       1.        ]), 'node_feat': array([['3.261', '32879.0'],
       ['2.659', '21146.0'],
       ['nan', '4408.4'],
       ['3.003', '18022.0'],
       ['3.4539999999999997', '9686.0'],
       ['3.227', '3373.0'],
       ['3.045', '18757.0'],
       ['3.1889999999999996', '1806.0'],
       ['2.8539999999999996', '9284.0'],
       ['3.284', '16714.0'],
       ['3.305', '15892.0'],
       ['2.8110000000000004', '2446.0'],
       ['2.944', '19852.0'],
       ['2.9760000000000004', '11833.0'],
       ['2.9219999999999997', '2570.0'],
       ['3.2', '16434.0'],
       ['nan', '55800.0'],
       ['3.01', '8043.0'],
       ['3.015', '3707.0'],
       ['nan', '619.4'],
       ['nan', '1928.3'],
       ['nan', '4319.5'],
       ['3.259', '1

{'labels': 0.19448175399999998, 'num_nodes': 84, 'num_edges': 4396, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 79., 80., 83.]]), 'edge_feat': array([1.        , 0.65301345, 0.62921873, ..., 0.56533837, 0.51550194,
       1.        ]), 'node_feat': array([['3.063', '25453.0'],
       ['2.439', '12966.0'],
       ['nan', '3577.8'],
       ['2.872', '13105.0'],
       ['3.344', '8443.0'],
       ['3.0660000000000003', '2466.0'],
       ['2.793', '10363.0'],
       ['3.772', '2675.0'],
       ['2.71', '11901.0'],
       ['3.009', '12486.0'],
       ['3.09', '15592.0'],
       ['2.827', '2805.0'],
       ['2.717', '18617.0'],
       ['2.968', '15338.0'],
       ['2.9760000000000004', '2882.0'],
       ['2.803', '10982.0'],
       ['nan', '58540.0'],
       ['2.8310000000000004', '6644.0'],
       ['2.611', '2842.0'],
       ['nan', '444.3'],
       ['nan', '1774.2'],
       ['nan', '3931.4'],
       ['2.968', '15505.0'],
       ['3.049', '2906.0'],

{'labels': -0.024350922999999997, 'num_nodes': 84, 'num_edges': 4322, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 79., 80., 83.]]), 'edge_feat': array([1.        , 0.50803299, 0.58089637, ..., 0.42576581, 0.47687957,
       1.        ]), 'node_feat': array([['3.0469999999999997', '32321.0'],
       ['2.4', '16701.0'],
       ['nan', '4360.2'],
       ['2.9010000000000002', '13741.0'],
       ['3.102', '9497.0'],
       ['3.2089999999999996', '3215.0'],
       ['2.943', '15062.0'],
       ['3.072', '1366.0'],
       ['2.8539999999999996', '14469.0'],
       ['3.017', '13440.0'],
       ['3.095', '16108.0'],
       ['2.807', '2153.0'],
       ['2.71', '16488.0'],
       ['2.819', '13824.0'],
       ['3.02', '3409.0'],
       ['2.8760000000000003', '14911.0'],
       ['nan', '61545.6'],
       ['2.798', '8242.0'],
       ['2.56', '3717.0'],
       ['nan', '577.4'],
       ['nan', '2344.0'],
       ['nan', '4487.0'],
       ['3.07', '15496.0'],
   

{'labels': 0.08506541599999999, 'num_nodes': 84, 'num_edges': 4338, 'edge_index': array([[ 0.,  0.,  0., ..., 83., 83., 83.],
       [ 0.,  1.,  2., ..., 80., 81., 83.]]), 'edge_feat': array([1.        , 0.57720661, 0.62081465, ..., 0.48833101, 0.59534922,
       1.        ]), 'node_feat': array([['3.284', '29435.0'],
       ['2.5989999999999998', '15323.0'],
       ['nan', '4269.0'],
       ['3.075', '12877.0'],
       ['3.375', '6664.0'],
       ['3.233', '1896.0'],
       ['2.9539999999999997', '10801.0'],
       ['3.242', '2153.0'],
       ['2.907', '7200.0'],
       ['3.115', '11453.0'],
       ['3.281', '13551.0'],
       ['2.9589999999999996', '2534.0'],
       ['2.85', '16771.0'],
       ['2.903', '8909.0'],
       ['2.4659999999999997', '1936.0'],
       ['3.1319999999999997', '11487.0'],
       ['nan', '50441.4'],
       ['2.9160000000000004', '8463.0'],
       ['2.727', '2574.0'],
       ['nan', '562.1'],
       ['nan', '1697.7'],
       ['nan', '3676.7'],
       ['3.388', '